# Evaluation on modified environement

1. Modify the environment.
2. Load the checkpoint - [docs](https://docs.ray.io/en/latest/serve/tutorials/rllib.html),
    - load RAY config,
    - build modified env,
    - Load the trained model.
3. Evaluate each seed 5 times.

## Ray startup

In [ ]:
import os

import ray
import ray.rllib.algorithms.ddpg as ddpg
import ray.rllib.algorithms.ppo as ppo
import ray.rllib.algorithms.sac as sac
import torch
from ray import serve

In [1]:
print(
    f">>> CUDA_VISIBLE_DEVICES environment variable: {os.environ['CUDA_VISIBLE_DEVICES']}"
)

# torch.cuda.is_available()
# GPU_ID = 0
# os.environ["CUDA_VISIBLE_DEVICES"] = str(GPU_ID)
# torch.cuda.set_device(GPU_ID)
print(
    f">>> That variable has been overwritten: {os.environ['CUDA_VISIBLE_DEVICES']}. Good luck, may AI be ever in your favour!"
)

>>> CUDA_VISIBLE_DEVICES environment variable: 0,1
>>> That variable has been overwritten: 0,1. Good luck, may AI be ever in your favour!


In [2]:
ray.shutdown()
ray.init(ignore_reinit_error=True, num_cpus=16, num_gpus=1, dashboard_host="0.0.0.0")

print(f">>>[torch] Version {torch.__version__}")
print(f">>>[torch] Avaiable GPUs: {torch.cuda.device_count()}")
print(f">>>[torch] Selected GPU (ID): {torch.cuda.current_device()}")
print(f">>>[ray] Version {ray.__version__}")
print(f">>>[ray] Allowed GPUs (IDs): {os.environ.get('CUDA_VISIBLE_DEVICES')}")
print(f">>>[ray] Ray resources: {ray.available_resources()}")
# print(f">>>[ray] Avaiable GPUs: {ray.get_gpu_ids()}")

print("Ray Dashboard URL: http://localhost:8265")

2023-05-19 12:17:56,225	INFO worker.py:1519 -- Started a local Ray instance. View the dashboard at 149.156.105.73:8266 


>>>[torch] Version 1.13.1+cu116
>>>[torch] Avaiable GPUs: 2
>>>[torch] Selected GPU (ID): 0
>>>[ray] Version 2.1.0
>>>[ray] Allowed GPUs (IDs): 0,1
>>>[ray] Ray resources: {'accelerator_type:G': 1.0, 'object_store_memory': 11204663705.0, 'GPU': 1.0, 'CPU': 16.0, 'memory': 43827670221.0, 'node:149.156.105.73': 1.0}
Ray Dashboard URL: http://localhost:8265


## Registering default envs

In [ ]:
import gym
from ray.rllib.env.wrappers.dm_control_wrapper import DMCEnv
from ray.tune.registry import register_env

from dm_control.suite import ALL_TASKS, BENCHMARKING, EXTRA

In [3]:
from_pixels = False
height = 64
width = 64
frame_skip = 2
channels_first = True
max_horizon = 1000  # dosen't work

env_list = []
DEFAULT_ENV_REGISTRY = {}
print(f">>> Registering DMC Envs...")
for env, task in BENCHMARKING:
    env_task_name = f"{env}-{task}"
    env_list.append(env_task_name)
    env_creator = lambda config: DMCEnv(
        env,
        task,
        from_pixels=from_pixels,
        height=height,
        width=width,
        frame_skip=frame_skip,
        channels_first=channels_first,
    )
    register_env(env_task_name, env_creator)
    DEFAULT_ENV_REGISTRY[env_task_name] = env_creator

print(env_list)
print(
    f'>>> Number of registered envs in RLlib: {len(env_list)} (from total of {len(BENCHMARKING)} from DMC suite "BENCHMARKING").'
)

>>> Registering DMC Envs...
['acrobot-swingup', 'acrobot-swingup_sparse', 'ball_in_cup-catch', 'cartpole-balance', 'cartpole-balance_sparse', 'cartpole-swingup', 'cartpole-swingup_sparse', 'cheetah-run', 'finger-spin', 'finger-turn_easy', 'finger-turn_hard', 'fish-upright', 'fish-swim', 'hopper-stand', 'hopper-hop', 'humanoid-stand', 'humanoid-walk', 'humanoid-run', 'manipulator-bring_ball', 'pendulum-swingup', 'point_mass-easy', 'reacher-easy', 'reacher-hard', 'swimmer-swimmer6', 'swimmer-swimmer15', 'walker-stand', 'walker-walk', 'walker-run']
>>> Number of registered envs in RLlib: 28 (from total of 28 from DMC suite "BENCHMARKING").


## Registering parametrized envs

In [ ]:
import copy
import inspect
from typing import List

from dmc_custom_envs import (
    acrobot,
    ball_in_cup,
    cartpole,
    cheetah,
    finger,
    fish,
    hopper,
    humanoid,
    manipulator,
    pendulum,
    point_mass,
    reacher,
    swimmer,
    walker,
)
from dmc_custom_envs.custom_dmc_env import CustomDMCEnv
from dmc_custom_envs.utils import load as dmc_suite_load

from dm_control.suite import _DOMAINS as DMC_DOMAINS
from dm_control.suite import _get_tasks as suite_get_tasks

In [5]:
# Refresh dm_control.suite internal dict of _DOMAINS
DMC_DOMAINS.update(
    {
        name: module
        for name, module in locals().items()
        if inspect.ismodule(module) and hasattr(module, "SUITE")
    }
)

BENCHMARKING_PARAM = suite_get_tasks(tag="benchmarking_param")
# THE NUMBER OF DISCRETE STEPS FOR EACH PARAMETER
# Idea: non-zero values, 20 steps
# IN PERCENTAGE
PARAM_RANGE = 20
PARAM_MIN = 0.1
PARAM_MAX = 2.0


def get_param_value(step: int) -> float:
    return PARAM_MIN + PARAM_MAX / PARAM_RANGE * step


PARAMETRIZED_ENVS = []
PARAMETRIZED_ENVS_REGISTRY = {}
print(f">>> Registering PARAMETRIZED DMC Envs...")

for env, task in BENCHMARKING_PARAM:
    for idx in range(0, PARAM_RANGE):
        env_task_name = f"{env}-{task}_{idx}"
        PARAMETRIZED_ENVS.append(env_task_name)

        params = {"value1": get_param_value(idx)}
        env_creator = lambda env=env, task=task, DMC_DOMAINS=DMC_DOMAINS, params=params: CustomDMCEnv(
            env,
            task,
            domains=DMC_DOMAINS,
            from_pixels=False,
            height=64,
            width=64,
            frame_skip=2,
            channels_first=True,
            environment_kwargs={"params": params},
        )
        plain_env_creator = (
            lambda env=env, task=task, DMC_DOMAINS=DMC_DOMAINS: dmc_suite_load(
                domain_name=env,
                task_name=task,
                domains=DMC_DOMAINS,
                task_kwargs=None,
                visualize_reward=False,
                environment_kwargs={"params": copy.deepcopy(params)},
            )
        )

        PARAMETRIZED_ENVS_REGISTRY[env_task_name] = env_creator
        register_env(env_task_name, env_creator)
    print(env_task_name)

print(
    f'>>> Number of registered envs from RLlib: {len(PARAMETRIZED_ENVS)} (from total of {len(BENCHMARKING_PARAM) * PARAM_RANGE} from DMC suite "BENCHMARKING_PARAM").'
)

>>> Registering PARAMETRIZED DMC Envs...
acrobot-swingup_param_19
acrobot-swingup_sparse_param_19
ball_in_cup-catch_param_19
cartpole-balance_param_19
cartpole-balance_sparse_param_19
cartpole-swingup_param_19
cartpole-swingup_sparse_param_19
cheetah-run_param_19
finger-spin_param_19
finger-turn_easy_param_19
finger-turn_hard_param_19
fish-upright_param_19
fish-swim_param_19
hopper-stand_param_19
hopper-hop_param_19
humanoid-stand_param_19
humanoid-walk_param_19
humanoid-run_param_19
manipulator-bring_ball_param_19
pendulum-swingup_param_19
point_mass-easy_param_19
reacher-easy_param_19
reacher-hard_param_19
swimmer-swimmer6_param_19
swimmer-swimmer15_param_19
walker-stand_param_19
walker-walk_param_19
walker-run_param_19
>>> Number of registered envs from RLlib: 560 (from total of 560 from DMC suite "BENCHMARKING_PARAM").


In [9]:
def get_parametrized_envs(env_task: str) -> List[str]:
    result = [x for x in PARAMETRIZED_ENVS if not x.find(f"{env_task}_param_")]
    if not result:
        raise KeyError("Task not found!")
    return result

## Loading configs & models

### Checkpoints

In [10]:
import json
import re
from pathlib import Path
from typing import Dict, Tuple

from starlette.requests import Request

In [12]:
# Load training config from jsons's parmameters

results_path = Path("/mnt/ws/eval_workdir_results")
CONFIGS = None


def load_results_configs(path: Path) -> Dict[str, Dict]:
    def get_task_env_name(directory_name: str) -> str:
        pattern = ".+?_(.+?)_[0-9,-]+_.+"
        return re.findall(pattern, directory.name)[0]

    algo_dirs = [
        x.name for x in results_path.iterdir() if x.name in ["SAC", "PPO", "DDPG"]
    ]

    result = {}
    for algo in algo_dirs:
        result[algo] = {} if result.get(algo, None) is None else result[algo]
        working_path = path.joinpath(algo)

        for directory in working_path.iterdir():
            env = get_task_env_name(directory.name)
            result[algo][env] = (
                {} if result[algo].get(env, None) is None else result[algo][env]
            )

            with working_path.joinpath(directory, "params.json").open("r") as json_file:
                result[algo][env] = json.load(json_file)

    return result


CONFIGS = load_results_configs(results_path)

print(f">>> CONFGS FOR TRAINED MODELS:")
print(f">> Number of registered algorithms: {len(CONFIGS)}")
for k, v in CONFIGS.items():
    print(f">> {k} task-envs: {len(v)}")

>>> CONFGS FOR TRAINED MODELS:
>> Number of registered algorithms: 3
>> DDPG task-envs: 28
>> SAC task-envs: 28
>> PPO task-envs: 28


In [13]:
# Append the latests checkpoint path to the model

checkpoints_path = Path("/mnt/ws/eval_workdir_checkpoints")


def get_models_paths(directory: Path) -> Dict[str, Dict[str, Dict[int, Path]]]:
    # returns Algo: Env: Seed: Path to the latestcheckpoint

    def get_env_and_seed(directory_name: str) -> Tuple[str, int]:
        pattern = r"(?P<env>.+?)_(?P<seed>\d+)"
        m = re.match(pattern, directory_name)
        return m.group("env"), int(m.group("seed"))

    def get_checkpoint_path(env_dir: Path) -> str:
        base = env_dir.joinpath("final_checkpoint")
        subdirs = sorted([str(x) for x in base.glob("./*")])
        return subdirs[-1]

    result = {}

    for algo_dir in directory.iterdir():
        algo = algo_dir.name

        if result.get(algo, None) is None:
            result[algo] = {}

        for env_dir in algo_dir.iterdir():
            env, seed = get_env_and_seed(env_dir.name)
            if result[algo].get(env, None) is None:
                result[algo][env] = {"checkpoints_paths": {}}
            result[algo][env]["checkpoints_paths"][seed] = str(
                get_checkpoint_path(env_dir)
            )

    return result


MODELS = get_models_paths(checkpoints_path)
print(f">>> Imported models paths.")


def assert_print(val1, val2, text: str) -> None:
    def bool2ok(x: bool) -> str:
        return " OK " if x else "NOK "

    ok = bool2ok(val1 == val2)
    print(f"[{ok}] {text}: {val1}/{val2}")


print(f">>>>>>>> CHECKPOINTS:")
print(f">>>>>> Number of registered algorithms: {len(MODELS)}")
for k, v in MODELS.items():
    for env_name, config in v.items():
        assert_print(
            len(config["checkpoints_paths"]), 5, f">> {k} task-env {env_name} seeds"
        )

assert Path(
    MODELS["PPO"]["fish-swim"]["checkpoints_paths"][0]
), "Can't read an example PPO fish-swim seed #0 !"

>>> Imported models paths.
>>>>>>>> CHECKPOINTS:
>>>>>> Number of registered algorithms: 3
[ OK ] >> DDPG task-env swimmer-swimmer6 seeds: 5/5
[ OK ] >> DDPG task-env humanoid-run seeds: 5/5
[ OK ] >> DDPG task-env fish-swim seeds: 5/5
[ OK ] >> DDPG task-env acrobot-swingup seeds: 5/5
[ OK ] >> DDPG task-env cartpole-swingup seeds: 5/5
[ OK ] >> DDPG task-env humanoid-walk seeds: 5/5
[ OK ] >> DDPG task-env reacher-easy seeds: 5/5
[ OK ] >> DDPG task-env cartpole-balance_sparse seeds: 5/5
[ OK ] >> DDPG task-env walker-walk seeds: 5/5
[ OK ] >> DDPG task-env manipulator-bring_ball seeds: 5/5
[ OK ] >> DDPG task-env acrobot-swingup_sparse seeds: 5/5
[ OK ] >> DDPG task-env swimmer-swimmer15 seeds: 5/5
[ OK ] >> DDPG task-env finger-turn_easy seeds: 5/5
[ OK ] >> DDPG task-env finger-spin seeds: 5/5
[ OK ] >> DDPG task-env cartpole-swingup_sparse seeds: 5/5
[ OK ] >> DDPG task-env point_mass-easy seeds: 5/5
[ OK ] >> DDPG task-env walker-run seeds: 5/5
[ OK ] >> DDPG task-env cartpole-b

### RLModel

In [ ]:
import copy
import csv
from datetime import datetime

import numpy as np
import torch

In [15]:
CONFIG_FROM_TRAINING = {
    "env": None,
    "horizon": 1000,
    "num_workers": 1,
    "framework": "torch",
    "model": {
        "fcnet_hiddens": [64, 64],
        "fcnet_activation": "relu",
    },
    "num_gpus": 1,
    "evaluation_num_workers": 1,
    "evaluation_config": {
        "render_env": False,
    },
    "evaluation_interval": 10,
    "log_level": "ERROR",
}

In [16]:
class EvaluationAlreadyDone(Exception):
    pass


# Hackery for Serve.deployment class
def RLModel_get_file_path(
    results_dir: Path, algo: str, env_name: str, task_name: str
) -> Path:
    return results_dir.joinpath(f"{algo}_{env_name}-{task_name}.csv")


# Hackery for Serve.deployment class
def RLModel_skip_already_done_evaluation(
    file_path: Path, param_step: int, seed: int
) -> None:
    rows = []
    with file_path.open("r") as csv_file:
        csv_reader = csv.DictReader(csv_file)
        for row in csv_reader:
            rows.append(row)
    if not rows:
        return
    last_row = rows[-1]

    last_param_step = int(last_row["step"])
    last_seed = int(last_row["seed"])

    if param_step < last_param_step:
        raise EvaluationAlreadyDone(
            f"Last step in CSV file: {last_param_step}, current step: {param_step}"
        )
    elif param_step == last_param_step:
        if seed <= last_seed:
            raise EvaluationAlreadyDone(
                f"Last seed in CSV file: {last_seed}, current seed: {seed}"
            )


# Slicing resources: 12 CPUs/12 =1 CPU, 8GBs of GPU's VRAM/12: = ~0.1 GPU
@serve.deployment(num_replicas=1, ray_actor_options={"num_cpus": 4.0, "num_gpus": 1.0})
class RLModel:
    def __init__(
        self,
        algo: str,
        seed: int,
        config: Dict,
        checkpoint_path: Path,
        results_output: Path,
    ):
        # Re-create the originally used config.
        self.config = config
        self.env_task_param_name = config["env"]
        self.algo = algo
        self.seed = seed
        self.env_name = self.config["env"].split("-")[0]
        task_param_name = self.config["env"].split("-")[1]
        self.task_name = "_".join(task_param_name.split("_")[:-2])
        self.param_step = int(task_param_name.split("_")[-1])
        self.results_filename = self.get_file_path(
            results_output, self.algo, self.env_name, self.task_name
        )

        self.NUMBER_OF_EVALUATIONS = 30

        self._prepare_csv_file()

        # Another hackery - lets try to fix it by using default env to create Algo
        config["env"] = f"{self.env_name}-{self.task_name}"

        # Build the Algorithm instance using the config.
        if self.algo == "DDPG":
            self.algorithm = ddpg.DDPG(config=config)
        elif self.algo == "PPO":
            self.algorithm = ppo.PPO(config=config)
        elif self.algo == "SAC":
            self.algorithm = sac.SAC(config=config)
        else:
            raise KeyError(f"Algorithm {self.algo} is not supported!")

        self.algorithm.restore(str(checkpoint_path))

        print(
            f"> Algorithm {self.algo} with {self.env_name} env for {self.task_name}_param_{self.param_step} task has been build."
        )

        self.input_shape = self.algorithm.get_policy().observation_space.shape

        print(f"> Checkpoint loaded.")
        print(f"> Preparing CSV file.")

        print(f"> Evaluating...")
        self._evaluation()
        print(f"> Evaluation done.")

    @classmethod
    def get_file_path(
        cls, results_dir: Path, algo: str, env_name: str, task_name: str
    ) -> Path:
        return results_dir.joinpath(f"{algo}_{env_name}-{task_name}.csv")

    def _prepare_csv_file(self) -> None:
        if self.results_filename.exists():
            return

        header = self._prepare_csv_header()
        with self.results_filename.open("w") as csv_file:
            csv_writer = csv.writer(csv_file)
            csv_writer.writerows(header)

    @classmethod
    def skip_already_done_evaluation(
        cls, file_path: Path, param_step: int, seed: int
    ) -> None:
        rows = []
        with file_path.open("r") as csv_file:
            csv_reader = csv.DictReader(csv_file)
            for row in csv_reader:
                rows.append(row)
        if not rows:
            return
        last_row = rows[-1]

        last_param_step = int(last_row["step"])
        last_seed = int(last_row["seed"])

        if param_step < last_param_step:
            raise EvaluationAlreadyDone(
                f"Last step in CSV file: {last_param_step}, current step: {param_step}"
            )
        elif param_step == last_param_step:
            if seed <= last_seed:
                raise EvaluationAlreadyDone(
                    f"Last seed in CSV file: {last_seed}, current seed: {seed}"
                )

    def _prepare_csv_header(self) -> List[List]:
        HEADER_BASE = [None] * (self.NUMBER_OF_EVALUATIONS + 2)
        HEADER_BASE[0] = "step"
        HEADER_BASE[1] = "seed"
        for x in range(self.NUMBER_OF_EVALUATIONS):
            HEADER_BASE[x + 2] = f"eval_score_no_{x}"
        return [HEADER_BASE]

    def _evaluation(self) -> None:
        env = PARAMETRIZED_ENVS_REGISTRY[self.env_task_param_name]()
        total_rewards = [None] * self.NUMBER_OF_EVALUATIONS

        for cnt in range(self.NUMBER_OF_EVALUATIONS):
            state = env.reset()
            done = False
            total_reward = 0.0
            while not done:
                action = self.algorithm.compute_single_action(state)
                state, reward, done, _ = env.step(action)
                total_reward += float(reward)

            total_rewards[cnt] = total_reward
            print(f"> Try #{cnt+1}: Total reward: {total_reward}")

        self._append_new_datarow(
            param_step=self.param_step, seed=self.seed, total_rewards=total_rewards
        )

    def _append_new_datarow(
        self, param_step: int, seed: int, total_rewards: int
    ) -> None:
        datarow = [None] * (self.NUMBER_OF_EVALUATIONS + 2)
        datarow[0] = param_step
        datarow[1] = seed
        for idx, reward in enumerate(total_rewards):
            datarow[idx + 2] = reward
        with self.results_filename.open("a") as csv_file:
            csv_writer = csv.writer(csv_file)
            csv_writer.writerows([datarow])

    async def __call__(self, request: Request) -> Dict:
        json_input = await request.json()
        obs = json_input["observation"]

        action = self.algorithm.compute_single_action(obs)
        return {"action": int(action)}


def models_generator(
    algo: str, env_config: Dict, models_paths: Dict, results_output: Path
):
    for seed, model_path in sorted(models_paths.items()):
        yield seed, RLModel.bind(algo, seed, env_config, model_path, results_output)

## Evaluation

In [19]:
algos = ["PPO"]
results_path = Path("/mnt/ws/eval_workdir_results")
reward_results_path = Path("/mnt/ws/eval_workdir_results/output")

for algo in algos:
    for env_task in CONFIGS[algo].keys():
        base_env_name = env_task.split("-")[0]
        try:
            get_parametrized_envs(env_task)
        except KeyError:
            # print(f">>>>>>>>>>[SKIPPING] {algo} | env_task: {env_task}")
            continue
        except ValueError:
            print(f">>>>>>>>>>[CRITICAL ERROR]: COULDNT LOAD {env_task} env_task !!!")
            continue

        env_config = CONFIGS[algo][env_task]
        models_paths = MODELS[algo][env_task]["checkpoints_paths"]

        print(f">>>>>>>>>> {algo} Eval | env_task: {env_task}")
        parametrized_envs = get_parametrized_envs(env_task)

        # Skip already done analysis
        maindir = [x for x in results_path.glob(f"{base_env_name}")]
        if maindir:
            print(
                f">>>>>>>> [SKIPPING] Found main env_task catalog (assuming completion)."
            )
            continue

        for param_env in parametrized_envs:
            config = copy.deepcopy(env_config)
            config["env"] = param_env
            print(f">>> Parametrized env_task: {config['env']}")

            env_name = config["env"].split("-")[0]
            _task_param_name = config["env"].split("-")[1]
            task_name = "_".join(_task_param_name.split("_")[:-2])
            param_step = int(_task_param_name.split("_")[-1])

            for seed, model in models_generator(
                algo, config, models_paths, reward_results_path
            ):
                print(f"> seed: {seed}")

                results_filename = RLModel_get_file_path(
                    reward_results_path, algo, env_name, task_name
                )
                try:
                    if results_filename.exists():
                        RLModel_skip_already_done_evaluation(
                            results_filename, param_step, seed
                        )
                except EvaluationAlreadyDone as e:
                    print(f"> SKIPPING according to the CSV results fire: {e}")
                    continue

                serve.run(model)

>>>>>>>>>> PPO Eval | env_task: cartpole-balance_sparse
>>> Parametrized env_task: cartpole-balance_sparse_param_0
> seed: 0
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 0
> seed: 5
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 0
> seed: 10
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 0
> seed: 15
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 0
> seed: 20
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 0
>>> Parametrized env_task: cartpole-balance_sparse_param_1
> seed: 0
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 1
> seed: 5
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 1
> seed: 10
> SKIPPING according to the CSV results fire: Last step in CSV file: 19, current step: 1
> seed: 15
> SKIPPING accordin

(ServeController pid=1594951) INFO 2023-05-19 12:17:57,593 controller 1594951 http_state.py:129 - Starting HTTP proxy with name 'SERVE_CONTROLLER_ACTOR:SERVE_PROXY_ACTOR-5e50c04eb9270146d6339e7c1d45d66d1338ad3e090d9b98769645c4' on node '5e50c04eb9270146d6339e7c1d45d66d1338ad3e090d9b98769645c4' listening on '127.0.0.1:8000'
(ServeController pid=1594951) INFO 2023-05-19 12:17:58,003 controller 1594951 deployment_state.py:1310 - Adding 1 replica to deployment 'RLModel'.
(HTTPProxyActor pid=1594976) INFO:     Started server process [1594976]
(ServeReplica:RLModel pid=1595006) 2023-05-19 12:17:59,198	WARNING ppo.py:351 -- `train_batch_size` (4000) cannot be achieved with your other settings (num_workers=8 num_envs_per_worker=1 rollout_fragment_length=200)! Auto-adjusting `rollout_fragment_length` to 500.
(ServeReplica:RLModel pid=1595006) 2023-05-19 12:17:59,198	INFO ppo.py:379 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simpl

(ServeReplica:RLModel pid=1595006) > Algorithm PPO with humanoid env for stand_param_0 task has been build.
(ServeReplica:RLModel pid=1595006) > Checkpoint loaded.
(ServeReplica:RLModel pid=1595006) > Preparing CSV file.
(ServeReplica:RLModel pid=1595006) > Evaluating...
(ServeReplica:RLModel pid=1595006) [dmc_custom_envs][DEBUG] File: humanoid.xml | Replacing '$GEAR' with '12.0'.


(ServeReplica:RLModel pid=1595006) 2023-05-19 12:18:03,068	INFO trainable.py:766 -- Restored on 149.156.105.73 from checkpoint: /mnt/ws/eval_workdir_checkpoints/PPO/humanoid-stand_0/final_checkpoint/checkpoint_000125
(ServeReplica:RLModel pid=1595006) 2023-05-19 12:18:03,068	INFO trainable.py:775 -- Current state after restoring: {'_iteration': 125, '_timesteps_total': None, '_time_total': 428.5977358818054, '_episodes_total': 1000}
(RolloutWorker pid=1595269) /home/user/miniconda/lib/python3.10/site-packages/ray/rllib/env/wrappers/dm_control_wrapper.py:49: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
(RolloutWorker pid=1595269) Deprecated in NumPy 1.20; for more det

(ServeReplica:RLModel pid=1595006) > Try #1: Total reward: 6.987191834943562
(ServeReplica:RLModel pid=1595006) > Try #2: Total reward: 6.342499096382232
(ServeReplica:RLModel pid=1595006) > Try #3: Total reward: 4.688840591848323
(ServeReplica:RLModel pid=1595006) > Try #4: Total reward: 7.249992004931649
(ServeReplica:RLModel pid=1595006) > Try #5: Total reward: 9.300364492696218
(ServeReplica:RLModel pid=1595006) > Try #6: Total reward: 7.497706423184823
(ServeReplica:RLModel pid=1595006) > Try #7: Total reward: 8.074083506090306
(ServeReplica:RLModel pid=1595006) > Try #8: Total reward: 2.420714798576011
(ServeReplica:RLModel pid=1595006) > Try #9: Total reward: 3.896759666214648
(ServeReplica:RLModel pid=1595006) > Try #10: Total reward: 0.9013865712923971
(ServeReplica:RLModel pid=1595006) > Try #11: Total reward: 6.304505071920165
(ServeReplica:RLModel pid=1595006) > Try #12: Total reward: 8.86995338216249
(ServeReplica:RLModel pid=1595006) > Try #13: Total reward: 4.67187825771

...

(ServeReplica:RLModel pid=1671285) > Algorithm PPO with humanoid env for run_param_19 task has been build.
(ServeReplica:RLModel pid=1671285) > Checkpoint loaded.
(ServeReplica:RLModel pid=1671285) > Preparing CSV file.
(ServeReplica:RLModel pid=1671285) > Evaluating...
(ServeReplica:RLModel pid=1671285) [dmc_custom_envs][DEBUG] File: humanoid.xml | Replacing '$GEAR' with '240.0'.
(ServeReplica:RLModel pid=1671285) > Try #1: Total reward: 0.532663130077272
(ServeReplica:RLModel pid=1671285) > Try #2: Total reward: 1.0417943986315013
(ServeReplica:RLModel pid=1671285) > Try #3: Total reward: 0.3355095485903095
(ServeReplica:RLModel pid=1671285) > Try #4: Total reward: 0.5784688514598948
(ServeReplica:RLModel pid=1671285) > Try #5: Total reward: 1.1022284178048
(ServeReplica:RLModel pid=1671285) > Try #6: Total reward: 0.2186872615734375
(ServeReplica:RLModel pid=1671285) > Try #7: Total reward: 1.546493845218177
(ServeReplica:RLModel pid=1671285) > Try #8: Total reward: 0.82326378123057

(ServeController pid=1594951) INFO 2023-05-19 13:34:36,970 controller 1594951 deployment_state.py:1214 - Stopping 1 replicas of deployment 'RLModel' with outdated versions.
(ServeController pid=1594951) INFO 2023-05-19 13:34:39,112 controller 1594951 deployment_state.py:1310 - Adding 1 replica to deployment 'RLModel'.
(ServeReplica:RLModel pid=1671671) 2023-05-19 13:34:40,303	WARNING ppo.py:351 -- `train_batch_size` (4000) cannot be achieved with your other settings (num_workers=8 num_envs_per_worker=1 rollout_fragment_length=200)! Auto-adjusting `rollout_fragment_length` to 500.
(ServeReplica:RLModel pid=1671671) 2023-05-19 13:34:40,303	INFO ppo.py:379 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(ServeReplica:RLModel pid=1671671) 2023-05-19 13:34:40,303	INFO algorithm.py:457 -- Current log_level is ERROR. For more information, set 'log_level': 'INFO' / 'DEBUG' or use th

(ServeReplica:RLModel pid=1671671) > Algorithm PPO with humanoid env for run_param_19 task has been build.
(ServeReplica:RLModel pid=1671671) > Checkpoint loaded.
(ServeReplica:RLModel pid=1671671) > Preparing CSV file.
(ServeReplica:RLModel pid=1671671) > Evaluating...
(ServeReplica:RLModel pid=1671671) [dmc_custom_envs][DEBUG] File: humanoid.xml | Replacing '$GEAR' with '240.0'.


(ServeReplica:RLModel pid=1671671) 2023-05-19 13:34:44,110	INFO trainable.py:766 -- Restored on 149.156.105.73 from checkpoint: /mnt/ws/eval_workdir_checkpoints/PPO/humanoid-run_20/final_checkpoint/checkpoint_000125
(ServeReplica:RLModel pid=1671671) 2023-05-19 13:34:44,110	INFO trainable.py:775 -- Current state after restoring: {'_iteration': 125, '_timesteps_total': None, '_time_total': 435.5413944721222, '_episodes_total': 1000}
(RolloutWorker pid=1671934) /home/user/miniconda/lib/python3.10/site-packages/ray/rllib/env/wrappers/dm_control_wrapper.py:49: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
(RolloutWorker pid=1671934) Deprecated in NumPy 1.20; for more deta

(ServeReplica:RLModel pid=1671671) > Try #1: Total reward: 0.018327385165929914
(ServeReplica:RLModel pid=1671671) > Try #2: Total reward: 1.1653720087497321
(ServeReplica:RLModel pid=1671671) > Try #3: Total reward: 0.3055889193093702
(ServeReplica:RLModel pid=1671671) > Try #4: Total reward: 0.4267303270994162
(ServeReplica:RLModel pid=1671671) > Try #5: Total reward: 1.4519488753265384
(ServeReplica:RLModel pid=1671671) > Try #6: Total reward: 1.4050160969603147
(ServeReplica:RLModel pid=1671671) > Try #7: Total reward: 0.6633946574858801
(ServeReplica:RLModel pid=1671671) > Try #8: Total reward: 0.8611501721953178
(ServeReplica:RLModel pid=1671671) > Try #9: Total reward: 0.19943236278226706
(ServeReplica:RLModel pid=1671671) > Try #10: Total reward: 0.938814427098704
(ServeReplica:RLModel pid=1671671) > Try #11: Total reward: 1.1400124772975944
(ServeReplica:RLModel pid=1671671) > Try #12: Total reward: 1.2532612269599115
(ServeReplica:RLModel pid=1671671) > Try #13: Total reward: